In [1]:
%load_ext autoreload
%autoreload 2

# Experiments with WMF followed by context-aware model
First learn user and item factors with WMF (optimal hyperparams known) then learn context factors with CA model.

In [2]:
from pathlib import Path
from functools import partial

from tqdm.auto import tqdm

import src.io as io
import src.evaluation as evaluation
import src.evaluation.splits
import src.evaluation.cars

from src.algorithm.baseline.wmf import WMF
from src.algorithm.cars.itals import iTALS, iTALSs
from src.algorithm.cars.wtf import WTF
from src.algorithm.cars.italsx import iTALSx

## Datasets

In [3]:
## RETARGET True for Frappe, False for the others
DATA_DIR, RETARGET = Path('../../../data/CARS/Mobile_Frappe/'), True

In [4]:
# Shouldn't need to change this info
INTERACTIONS = DATA_DIR / 'interactions.csv'

SEED = 123456
SEED2 = 78910

ITEM_ID = 'item'
USER_ID = 'user'

MODELS = {
    'iTALS one': partial(iTALS, default_context_1=True, max_iterations=3),
    'iTALS': partial(iTALS, default_context_1=False, max_iterations=3),
    'iTALSs one': partial(iTALSs, default_context_1=True),
    'iTALSs': partial(iTALSs, default_context_1=False),
    'WTF one': partial(WTF, default_context_1=True, max_cg_iter=10),
    'WTF': partial(WTF, default_context_1=False, max_cg_iter=10),
    'iTALSx': iTALSx
}

## Provider of WMF factors for all models

In [5]:
K = 80
WMF_MAX_IT = 10

# depends on dataset
WMF_L2 = 100
WMF_V = 0.25
WMF_ALPHA = 500

WMF_HYPERPARAMS = {'k': K, 'l2': WMF_L2, 'v': WMF_V, 'alpha': WMF_ALPHA, 'max_iterations': WMF_MAX_IT}

In [6]:
# map seed to learned factors
userItemFactorCache = dict()
def userItemFactorSupplier(data, seed):
    if seed not in userItemFactorCache:
        print("Computing factors WMF")
        wmf = WMF(**WMF_HYPERPARAMS)
        wmf.fit(data.toCSR())
        P, Q = wmf.getUserItemFactors()
        userItemFactorCache[seed] = (P, Q)
        
    return userItemFactorCache[seed]

## Define algorithm and hyperparameter ranges

In [7]:
L2 = [1, 10, 100, 1000, 10000]
V = [0, 0.25, 0.5, 0.75, 1]
ALPHA = [1, 10, 100, 1000, 10000]


HYPERPARAMS = {'k': K, 'l2': L2, 'v': V, 'alpha': ALPHA}
HYPERPARAMS

{'k': 80,
 'l2': [1, 10, 100, 1000, 10000],
 'v': [0, 0.25, 0.5, 0.75, 1],
 'alpha': [1, 10, 100, 1000, 10000]}

## Parse data

In [8]:
data = io.parse_interactions_with_context(INTERACTIONS, item_id=ITEM_ID, user_id=USER_ID)

## Make train/val split for hyperparam tuning

In [9]:
train, test = evaluation.splits.context_leave_one_out_split(data, seed=SEED)

## Perform gridsearch on validation set

In [10]:
P, Q = userItemFactorSupplier(train, SEED)

Computing factors WMF


  0%|          | 0/10 [00:00<?, ?it/s]

In [11]:
%%time
modelHyperparams = dict()
for modelName, Model in tqdm(MODELS.items()):
    score, bestHyperparams = evaluation.cars.gridsearchSetFactors(Model, train, test, P, Q, HYPERPARAMS, retarget=RETARGET)
    print(f"Best score of {score} for model {modelName} achieved with {bestHyperparams}.")
    modelHyperparams[modelName] = bestHyperparams

  0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/125 [00:00<?, ?it/s]

Training model <src.algorithm.cars.itals.iTALS object at 0x7f9437005250> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}


  0%|          | 0/3 [00:00<?, ?it/s]

Evaluating with 816 users
MRR@5 0.157
MRR@20 0.182
Average Recall@5 0.268
Average Recall@20 0.499
Training model <src.algorithm.cars.itals.iTALS object at 0x7f9437001400> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}


...

Training model <src.algorithm.cars.wtf.WTF object at 0x7f9426fbea90> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.248
MRR@20 0.274
Average Recall@5 0.402
Average Recall@20 0.654
Training model <src.algorithm.cars.wtf.WTF object at 0x7f94269587c0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.248
MRR@20 0.273
Average Recall@5 0.404
Average Recall@20 0.657
Training model <src.algorithm.cars.wtf.WTF object at 0x7f9426a4a310> with hyperparameters {'k': 80, 'l2': 100, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.25
MRR@20 0.278
Average Recall@5 0.411
Average Recall@20 0.659
Training model <src.algorithm.cars.wtf.WTF object at 0x7f942713b8b0> with hyperparameters {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.216
MRR@20 0.244
Average Recall@5 0.371
Average Recall@20 0.642
Training model <src.algorithm.cars.wtf.WTF object at 0x7f9427512760> with hyperparamete

  0%|          | 0/125 [00:00<?, ?it/s]

Training model <src.algorithm.cars.wtf.WTF object at 0x7f9427051910> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.247
MRR@20 0.273
Average Recall@5 0.407
Average Recall@20 0.652
Training model <src.algorithm.cars.wtf.WTF object at 0x7f942688e6d0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.243
MRR@20 0.269
Average Recall@5 0.406
Average Recall@20 0.648
Training model <src.algorithm.cars.wtf.WTF object at 0x7f94276d0af0> with hyperparameters {'k': 80, 'l2': 100, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.239
MRR@20 0.264
Average Recall@5 0.4
Average Recall@20 0.645
Training model <src.algorithm.cars.wtf.WTF object at 0x7f943478a2b0> with hyperparameters {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.206
MRR@20 0.228
Average Recall@5 0.355
Average Recall@20 0.571
Training model <src.algorithm.cars.wtf.WTF object at 0x7f9426a0f670> with hyperparameter

  0%|          | 0/125 [00:00<?, ?it/s]

Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f9426a4a460> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.174
MRR@20 0.202
Average Recall@5 0.312
Average Recall@20 0.597
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f9426d4eca0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.174
MRR@20 0.202
Average Recall@5 0.312
Average Recall@20 0.596
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f94273e6430> with hyperparameters {'k': 80, 'l2': 100, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.174
MRR@20 0.201
Average Recall@5 0.312
Average Recall@20 0.596
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f94276630d0> with hyperparameters {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1}
Evaluating with 816 users
MRR@5 0.174
MRR@20 0.202
Average Recall@5 0.312
Average Recall@20 0.597
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7

## Evaluate models with optimal hyperparams with KFolds Cross validation

In [12]:
%%time

for modelName, Model in MODELS.items():
    print()
    bestHyperparams = modelHyperparams[modelName]
    alg = Model(**bestHyperparams)
    results = evaluation.cars.contextKFoldsSetFactorsEval(alg, data, userItemFactorSupplier, nr_folds=5, seed=SEED2, retarget=RETARGET)
    print("Model:", modelName)
    print("Hyperparams:", bestHyperparams)
    evaluation.cars.printKfoldsMetrics(results)


Computing factors WMF


  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/3 [00:00<?, ?it/s]

Evaluating with 816 users
Computing factors WMF


  0%|          | 0/10 [00:00<?, ?it/s]

...

Evaluating with 816 users


  0%|          | 0/10 [00:00<?, ?it/s]

Evaluating with 816 users


  0%|          | 0/10 [00:00<?, ?it/s]

Evaluating with 816 users
Model: iTALSs
Hyperparams: {'k': 80, 'l2': 1, 'v': 1, 'alpha': 1}
MRR@5 0.198 (0.008)
MRR@20 0.226 (0.008)
Average Recall@5 0.362 (0.011)
Average Recall@20 0.626 (0.018)

Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Model: WTF one
Hyperparams: {'k': 80, 'l2': 1, 'v': 1, 'alpha': 10}
MRR@5 0.242 (0.01)
MRR@20 0.266 (0.01)
Average Recall@5 0.416 (0.007)
Average Recall@20 0.647 (0.013)

Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Model: WTF
Hyperparams: {'k': 80, 'l2': 1, 'v': 1, 'alpha': 10}
MRR@5 0.24 (0.008)
MRR@20 0.265 (0.008)
Average Recall@5 0.417 (0.006)
Average Recall@20 0.65 (0.015)

Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Evaluating with 816 users
Model: iTALSx
Hyperparams: {'k': 80, 'l2': 1, 'v': 0, 'alpha': 100}
MRR@5 0